# Load Markets for One Specific Event


In [5]:
import requests, json

event_ticker = "KXPRESPERSON-28"
url = f"https://api.elections.kalshi.com/trade-api/v2/events/{event_ticker}?with_nested_markets=true"
response = requests.get(url)
oneEventMarkets = response.json()
print(json.dumps(oneEventMarkets, indent=4))

{
    "event": {
        "available_on_brokers": true,
        "category": "Elections",
        "collateral_return_type": "MECNET",
        "event_ticker": "KXPRESPERSON-28",
        "markets": [
            {
                "can_close_early": true,
                "close_time": "2029-11-07T15:00:00Z",
                "created_time": "0001-01-01T00:00:00Z",
                "custom_strike": {
                    "Pres candidate": "Gavin Newsom"
                },
                "early_close_condition": "This market will close and expire after a person has been inaugurated as President pursuant to the next presidential election.",
                "event_ticker": "KXPRESPERSON-28",
                "expected_expiration_time": "2029-01-21T15:00:00Z",
                "expiration_time": "2029-11-07T15:00:00Z",
                "expiration_value": "",
                "last_price": 20,
                "last_price_dollars": "0.2000",
                "latest_expiration_time": "2029-11-07T15:00:0

In [ ]:
# Converting Events and Markets to DataFrames:
import pandas as pd
pd.set_option('display.max_columns', None)
events_df = pd.json_normalize(oneEventMarkets["event"])
events_df.head()

available_on_brokers   category collateral_return_type     event_ticker  \
0                  True  Elections                 MECNET  KXPRESPERSON-28   

                                             markets  mutually_exclusive  \
0  [{'can_close_early': True, 'close_time': '2029...                True   

  series_ticker strike_period sub_title  \
0  KXPRESPERSON                 In 2028   

                                     title  
0  Next U.S. Presidential Election Winner?

In [ ]:
import psycopg2

# connection establishment
conn = psycopg2.connect(
   database="postgres",
    user='postgres',
    password='kek',
    host='localhost',
    port= '5432'
)

conn.autocommit = True

# Creating a cursor object
cursor = conn.cursor()

# query to create a database 
sql = """
    Create table if not exists events (
        event_ticker TEXT PRIMARY KEY,
        series_ticker TEXT,
        title TEXT,
        sub_title TEXT,
        category TEXT,
        available_on_brokers BOOLEAN,
        mutually_exclusive BOOLEAN,
        collateral_return_type TEXT,
        strike_period TEXT,
        updated_at TIMESTAMPTZ DEFAULT now()
    );

    
    CREATE TABLE IF NOT EXISTS markets (
        market_ticker TEXT PRIMARY KEY,
        event_ticker TEXT,

        title       TEXT,
        subtitle    TEXT,
        market_type TEXT,                                
        status      TEXT, 

        can_close_early BOOLEAN,
        tick_size       SMALLINT,
        settlement_timer_seconds INTEGER, 

        open_time                TIMESTAMPTZ,
        close_time               TIMESTAMPTZ,
        expiration_time          TIMESTAMPTZ,
        expected_expiration_time TIMESTAMPTZ,
        latest_expiration_time   TIMESTAMPTZ,
        created_time             TIMESTAMPTZ,

        
        last_price     SMALLINT,
        previous_price SMALLINT,
        yes_ask        SMALLINT,
        yes_bid        SMALLINT,
        no_ask         SMALLINT,
        no_bid         SMALLINT,
        previous_yes_ask SMALLINT,
        previous_yes_bid SMALLINT,

        last_price_dollars       NUMERIC(10,4),
        previous_price_dollars   NUMERIC(10,4),
        yes_ask_dollars          NUMERIC(10,4),
        yes_bid_dollars          NUMERIC(10,4),
        no_ask_dollars           NUMERIC(10,4),
        no_bid_dollars           NUMERIC(10,4),
        previous_yes_ask_dollars NUMERIC(10,4),
        previous_yes_bid_dollars NUMERIC(10,4),

        
        liquidity        BIGINT,                         
        open_interest    BIGINT,
        volume           BIGINT,
        volume_24h       BIGINT,

        liquidity_dollars    NUMERIC(20,4),
        open_interest_fp     NUMERIC(20,2),
        volume_fp            NUMERIC(20,2),
        volume_24h_fp         NUMERIC(20,2),

        price_level_structure TEXT,                      
        response_price_units  TEXT,                       
        expiration_value      TEXT,
        result                TEXT,

        no_sub_title  TEXT,
        yes_sub_title TEXT,

        early_close_condition TEXT,
        rules_primary         TEXT,
        rules_secondary       TEXT,

        price_ranges JSONB,                              
        custom_strike JSONB,                             

        updated_at TIMESTAMPTZ DEFAULT now(), 

        CONSTRAINT fk_markets_event
            FOREIGN KEY(event_ticker)
            REFERENCES events(event_ticker)
            ON DELETE CASCADE
    );

    CREATE INDEX IF NOT EXISTS idx_markets_event_ticker ON markets(event_ticker);
    CREATE INDEX IF NOT EXISTS idx_markets_status ON markets(status);


    CREATE TABLE IF NOT EXISTS candles (
        market_ticker TEXT NOT NULL,
        interval_min  INTEGER NOT NULL,           -- period_interval you requested (1, 60, 1440, etc.)
        end_ts        TIMESTAMPTZ NOT NULL,        -- derived from end_period_ts (unix seconds)

        -- trades (may be NULL if no trades in bucket)
        trade_open    SMALLINT,
        trade_high    SMALLINT,
        trade_low     SMALLINT,
        trade_close   SMALLINT,
        trade_prev    SMALLINT,                   -- price.previous

        -- bid/ask quote candles (usually present)
        yes_bid_open  SMALLINT,
        yes_bid_high  SMALLINT,
        yes_bid_low   SMALLINT,
        yes_bid_close SMALLINT,

        yes_ask_open  SMALLINT,
        yes_ask_high  SMALLINT,
        yes_ask_low   SMALLINT,
        yes_ask_close SMALLINT,

        -- activity
        volume        BIGINT NOT NULL DEFAULT 0,
        open_interest BIGINT,

        created_at    TIMESTAMPTZ NOT NULL DEFAULT now(),


        CONSTRAINT pk_candles PRIMARY KEY (market_ticker, interval_min, end_ts),
        CONSTRAINT fk_candles_market FOREIGN KEY (market_ticker)
            REFERENCES markets(market_ticker)
            ON DELETE CASCADE
    );

    CREATE INDEX IF NOT EXISTS idx_candles_market_interval_endts
    ON candles (market_ticker, interval_min, end_ts DESC);

    """;

# executing above query
cursor.execute(sql)
print("Database has been created successfully !!!");

# Print
with conn, conn.cursor() as cur:
    cur.execute("SELECT * FROM postgres;")
    databases = cur.fetchall()
    for database in databases:
        print(database)
# Closing the connection
conn.close()

DuplicateDatabase: database "kalshidb" already exists


In [23]:
pd.set_option('display.max_columns', None)
markets_df = pd.json_normalize(oneEventMarkets["event"]["markets"], sep=".")
markets_df["event_ticker"] = oneEventMarkets["event"]["event_ticker"]
markets_df.head(30)

can_close_early            close_time          created_time  \
0              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
1              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
2              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
3              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
4              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
5              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
6              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
7              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
8              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
9              True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
10             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
11             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
12             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
13             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
14             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
15             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
16             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
17             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
18             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
19             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
20             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
21             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   
22             True  2029-11-07T15:00:00Z  0001-01-01T00:00:00Z   

                                early_close_condition     event_ticker  \
0   This market will close and expire after a pers...  KXPRESPERSON-28   
1   This market will close and expire after a pers...  KXPRESPERSON-28   
2   This market will close and expire after a pers...  KXPRESPERSON-28   
3   This market will close and expire after a pers...  KXPRESPERSON-28   
4   This market will close and expire after a pers...  KXPRESPERSON-28   
5   This market will close and expire after a pers...  KXPRESPERSON-28   
6   This market will close and expire after a pers...  KXPRESPERSON-28   
7   This market will close and expire after a pers...  KXPRESPERSON-28   
8   This market will close and expire after a pers...  KXPRESPERSON-28   
9   This market will close and expire after a pers...  KXPRESPERSON-28   
10  This market will close and expire after a pers...  KXPRESPERSON-28   
11  This market will close and expire after a pers...  KXPRESPERSON-28   
12  This market will close and expire after a pers...  KXPRESPERSON-28   
13  This market will close and expire after a pers...  KXPRESPERSON-28   
14  This market will close and expire after a pers...  KXPRESPERSON-28   
15  This market will close and expire after a pers...  KXPRESPERSON-28   
16  This market will close and expire after a pers...  KXPRESPERSON-28   
17  This market will close and expire after a pers...  KXPRESPERSON-28   
18  This market will close and expire after a pers...  KXPRESPERSON-28   
19  This market will close and expire after a pers...  KXPRESPERSON-28   
20  This market will close and expire after a pers...  KXPRESPERSON-28   
21  This market will close and expire after a pers...  KXPRESPERSON-28   
22  This market will close and expire after a pers...  KXPRESPERSON-28   

   expected_expiration_time       expiration_time expiration_value  \
0      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z                    
1      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z                    
2      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z                    
3      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z                    
4      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z                    
5      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z                    
6      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z                    
7      2029-01-21T15:00:00Z  2029-11-07T15:00:00Z         

In [27]:
import requests
from datetime import datetime, timezone

marketsCandles = {}


for market in oneEventMarkets["event"]["markets"]:
    market_ticker = market["ticker"]
    now_utc = datetime.now(timezone.utc)
    created_time = int(datetime.fromisoformat(market["created_time"].replace("Z", "+00:00")).timestamp())
    end_ts = int(now_utc.timestamp())
    start_ts = (end_ts - 24*60*60) if created_time <= (end_ts - 24*60*60) else created_time
    interval = 1

    params = {
        "market_tickers": market_ticker,   
        "start_ts": start_ts,
        "end_ts": end_ts,
        "period_interval": 1,              
        "include_latest_before_start": "true",
    }
    
    url = f"https://api.elections.kalshi.com/trade-api/v2/markets/candlesticks"
    try:
        response = requests.get(url, params=params, timeout=10)
        oneMarketCandles = response.json()
        marketsCandles[market_ticker] = oneMarketCandles
    except Exception as e:
        print(f"Error fetching markets for event {event_ticker}: {e}")
print(json.dumps(marketsCandles, indent=4))

{
    "KXPRESPERSON-28-GNEWS": {
        "markets": [
            {
                "candlesticks": [
                    {
                        "end_period_ts": 1769535360,
                        "open_interest": 638903,
                        "open_interest_fp": "638903.00",
                        "price": {
                            "close": null,
                            "high": null,
                            "low": null,
                            "max": null,
                            "mean": null,
                            "min": null,
                            "open": null,
                            "previous": 20,
                            "previous_dollars": "0.2000"
                        },
                        "volume": 0,
                        "volume_fp": "0.00",
                        "yes_ask": {
                            "close": 20,
                            "close_dollars": "0.2000",
                            "high": 20,
       